In [3]:
import numpy as np
import tensorflow as tf
import os
import json


In [4]:
data_dir='..//..//二维高熵合金数据'

embedding_path = os.path.join(data_dir, 'alloy_embedding_matrices.npy')
X_all = np.load(embedding_path)

hv_path = os.path.join(data_dir, 'HV_values.npy')
Y_all = np.load(hv_path)

info_path = os.path.join(data_dir, 'data_info.json')
with open(info_path, 'r', encoding='utf-8') as f:
    data_info = json.load(f)

print(f"✓ 数据加载完成")
print(f"  样本数量: {len(X_all)}")
print(f"  嵌入矩阵形状: {X_all.shape}")
print(f"  HV值范围: [{Y_all.min():.2f}, {Y_all.max():.2f}]")

X_all = np.expand_dims(X_all, axis=1)
print(f"  调整后形状: {X_all.shape}")

✓ 数据加载完成
  样本数量: 483
  嵌入矩阵形状: (483, 21, 768)
  HV值范围: [109.00, 1084.00]
  调整后形状: (483, 1, 21, 768)


In [8]:
for i in range(len(X_all[0][0])):
    print(X_all[0][0][i])

[-0.  0.  0. -0.  0. -0. -0.  0. -0. -0.  0.  0.  0.  0. -0. -0.  0. -0.
 -0. -0. -0. -0.  0. -0. -0. -0.  0.  0.  0. -0.  0. -0. -0.  0. -0.  0.
  0.  0. -0.  0. -0.  0.  0.  0. -0.  0. -0. -0. -0. -0.  0. -0.  0.  0.
  0. -0. -0. -0.  0.  0.  0.  0. -0.  0. -0. -0. -0.  0.  0. -0.  0. -0.
  0.  0. -0. -0.  0. -0.  0.  0.  0. -0. -0. -0. -0. -0.  0.  0.  0. -0.
 -0. -0. -0. -0. -0. -0. -0. -0. -0.  0.  0.  0.  0.  0. -0. -0.  0.  0.
 -0.  0.  0. -0.  0.  0. -0.  0. -0. -0. -0.  0. -0.  0. -0.  0. -0.  0.
 -0.  0.  0.  0. -0. -0. -0. -0.  0.  0. -0.  0. -0.  0.  0. -0. -0.  0.
 -0.  0. -0. -0.  0.  0.  0. -0. -0.  0.  0.  0.  0. -0.  0.  0. -0. -0.
  0. -0.  0.  0. -0. -0. -0.  0. -0. -0. -0. -0.  0.  0.  0.  0.  0.  0.
  0. -0.  0.  0.  0.  0. -0.  0. -0. -0.  0.  0. -0.  0. -0.  0. -0.  0.
 -0. -0. -0.  0. -0.  0.  0. -0.  0.  0. -0.  0. -0.  0. -0.  0.  0.  0.
 -0. -0. -0.  0. -0. -0.  0.  0. -0. -0. -0.  0. -0. -0. -0.  0. -0. -0.
 -0.  0. -0.  0. -0. -0.  0.  0. -0. -0.  0.  0.  0

In [1]:
# 在所有导入之前
import os
os.environ['PYTHONHASHSEED'] = '42'
os.environ['TF_DETERMINISTIC_OPS'] = '1'
os.environ['TF_CUDNN_DETERMINISTIC'] = '1'

# 然后再导入其他库
import numpy as np
import tensorflow as tf
import os
import json
import csv
import matplotlib.pyplot as plt
from sklearn.model_selection import KFold
from sklearn.metrics import mean_absolute_error, mean_squared_error
import tensorflow as tf
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout, BatchNormalization

# 设置中文字体
import matplotlib
matplotlib.rcParams['font.sans-serif'] = ['SimHei', 'DejaVu Sans']
matplotlib.rcParams['axes.unicode_minus'] = False

# 2. 在set_random_seeds函数中添加GPU配置
def set_random_seeds(seed):
    """设置所有可能的随机种子"""
    import random
    random.seed(seed)
    np.random.seed(seed)
    tf.random.set_seed(seed)
    
    os.environ['TF_DETERMINISTIC_OPS'] = '1'
    os.environ['TF_CUDNN_DETERMINISTIC'] = '1'
    os.environ['PYTHONHASHSEED'] = str(seed)
    
    tf.keras.utils.set_random_seed(seed)
    tf.config.experimental.enable_op_determinism()
    
    # 添加GPU内存配置
    gpus = tf.config.list_physical_devices('GPU')
    if gpus:
        try:
            for gpu in gpus:
                tf.config.experimental.set_memory_growth(gpu, True)
        except RuntimeError as e:
            print(f"GPU配置警告: {e}")

# 设置随机种子
SEED = 20
set_random_seeds(SEED)

# 输入输出目录
output_dir = './best_model_final_0'


# ============================================================================
# 1. 数据加载函数
# ============================================================================
def load_embedding_data(data_dir='..//..//二维高熵合金数据'):
    """加载生成的嵌入矩阵数据"""
    print("="*60)
    print("加载数据...")
    print("="*60)
    
    embedding_path = os.path.join(data_dir, 'alloy_embedding_matrices.npy')
    X_all = np.load(embedding_path)
    
    hv_path = os.path.join(data_dir, 'HV_values.npy')
    Y_all = np.load(hv_path)
    
    info_path = os.path.join(data_dir, 'data_info.json')
    with open(info_path, 'r', encoding='utf-8') as f:
        data_info = json.load(f)
    
    print(f"✓ 数据加载完成")
    print(f"  样本数量: {len(X_all)}")
    print(f"  嵌入矩阵形状: {X_all.shape}")
    print(f"  HV值范围: [{Y_all.min():.2f}, {Y_all.max():.2f}]")
    
    X_all = np.expand_dims(X_all, axis=1)
    print(f"  调整后形状: {X_all.shape}")
    
    return X_all, Y_all, data_info

# ============================================================================
# 2. CNN模型构建函数
# ============================================================================
def build_cnn_model(input_shape, hyperparams):
    """根据超参数构建CNN模型"""
    model = Sequential()
    
    conv_filters = hyperparams['conv_filters']
    kernel_size = hyperparams['kernel_size']
    use_batch_norm = hyperparams['use_batch_norm']
    dropout_rate = hyperparams['dropout_rate']
    activation = hyperparams['activation']
    
    # 第一个卷积层
    model.add(Conv2D(
        filters=conv_filters[0],
        kernel_size=kernel_size,
        strides=1,
        padding='same',
        data_format='channels_first',
        activation=activation,
        input_shape=input_shape
    ))
    if use_batch_norm:
        model.add(BatchNormalization(axis=1))
    model.add(MaxPooling2D(pool_size=(2, 2), strides=2, padding='same', 
                           data_format='channels_first'))
    
    # 第二个卷积层
    model.add(Conv2D(conv_filters[1], kernel_size, strides=1, padding='same',
                     data_format='channels_first', activation=activation))
    if use_batch_norm:
        model.add(BatchNormalization(axis=1))
    model.add(MaxPooling2D((2, 2), 2, 'same', data_format='channels_first'))
    
    # 第三个卷积层
    model.add(Conv2D(conv_filters[2], kernel_size, strides=1, padding='same',
                     data_format='channels_first', activation=activation))
    if use_batch_norm:
        model.add(BatchNormalization(axis=1))
    model.add(MaxPooling2D((2, 2), 2, 'same', data_format='channels_first'))
    
    # 展平
    model.add(Flatten())
    
    # 全连接层
    dense_units = hyperparams['dense_units']
    for units in dense_units:
        model.add(Dense(units, activation=activation))
        if dropout_rate > 0:
            model.add(Dropout(dropout_rate))
    
    # 输出层
    model.add(Dense(1, activation='linear'))
    
    # 编译模型
    adam = Adam(learning_rate=hyperparams['learning_rate'])
    model.compile(
        optimizer=adam, 
        loss='mean_squared_error',
        metrics=[
            tf.keras.metrics.RootMeanSquaredError(),
            tf.keras.metrics.MeanAbsoluteError()
        ]
    )
    
    return model

# ============================================================================
# 3. 使用最佳参数进行完整训练
# ============================================================================
def train_with_best_params(X_all, Y_all, best_params, output_dir='./best_model_results'):
    """使用最佳参数进行完整的十折交叉验证训练"""
    os.makedirs(output_dir, exist_ok=True)
    
    print("\n" + "="*60)
    print("使用最佳参数进行完整训练")
    print("="*60)
    print(f"\n最佳参数:")
    for k, v in best_params.items():
        if k in ['conv_filters', 'dense_units']:
            print(f"  {k}: {list(v)}")
        else:
            print(f"  {k}: {v}")
    print("="*60)
    
    kf = KFold(n_splits=10, random_state=2*10+55, shuffle=True)
    
    all_rmse = []
    all_mae = []
    all_r2 = []
    
    results_file = os.path.join(output_dir, 'training_results.csv')
    with open(results_file, 'w', newline='') as f:
        writer = csv.writer(f)
        writer.writerow(['fold', 'loss_train', 'loss_test', 'r_train', 
                        'r_test', 'mae', 'rmse'])
    
    # 创建每折预测结果保存目录
    predictions_dir = os.path.join(output_dir, 'fold_predictions')
    os.makedirs(predictions_dir, exist_ok=True)
    
    for fold, (train_idx, test_idx) in enumerate(kf.split(X_all)):
        print(f"\n第 {fold + 1}/10 折")
        
        x_train, x_test = X_all[train_idx], X_all[test_idx]
        y_train, y_test = Y_all[train_idx], Y_all[test_idx]
        
        # 保存每折的模型
        model_path = os.path.join(output_dir, f'best_model_fold_{fold}.h5')
        
        callbacks = [
            # EarlyStopping(
            #     monitor='val_loss',
            #     patience=30,
            #     min_delta=0.0001,
            #     restore_best_weights=True,
            #     verbose=1,
            #     mode='min'
            # ),
            ModelCheckpoint(
                filepath=model_path,
                monitor='val_loss',
                save_best_only=True,
                mode='min',
                verbose=1
            )
        ]
        
        input_shape = x_train.shape[1:]
        model = build_cnn_model(input_shape, best_params)
        
        history = model.fit(
            x_train, y_train,
            epochs=500,
            batch_size=best_params['batch_size'],
            validation_data=(x_train, y_train),
            callbacks=callbacks,
            verbose=1
        )
        
        # 加载最佳模型
        model = load_model(model_path)
        
        loss_train, rmse_train, mae_train = model.evaluate(x_train, y_train, verbose=0)
        loss_test, rmse_test, mae_test = model.evaluate(x_test, y_test, verbose=0)
        
        # 预测
        pred_train = model.predict(x_train, batch_size=best_params['batch_size'], verbose=0).reshape(-1)
        pred_test = model.predict(x_test, batch_size=best_params['batch_size'], verbose=0).reshape(-1)
        
        r_train = np.corrcoef(pred_train, y_train)[0, 1]
        r_test = np.corrcoef(pred_test, y_test)[0, 1]
        
        mae = mean_absolute_error(y_test, pred_test)
        rmse = mean_squared_error(y_test, pred_test) ** 0.5
        
        all_rmse.append(rmse)
        all_mae.append(mae)
        all_r2.append(r_test)
        
        print(f"  测试集 R: {r_test:.4f}, MAE: {mae:.4f}, RMSE: {rmse:.4f}")
        
        with open(results_file, 'a', newline='') as f:
            writer = csv.writer(f)
            writer.writerow([fold, loss_train, loss_test, r_train, r_test, mae, rmse])
        
        # ========== 保存训练集预测结果 ==========
        train_predictions_file = os.path.join(predictions_dir, f'fold_{fold}_train_predictions.csv')
        with open(train_predictions_file, 'w', newline='') as f:
            writer = csv.writer(f)
            writer.writerow(['original_index', 'true_value', 'predicted_value', 'error'])
            for idx, true_val, pred_val in zip(train_idx, y_train, pred_train):
                writer.writerow([idx, true_val, pred_val, abs(true_val - pred_val)])
        
        # ========== 保存验证集(测试集)预测结果 ==========
        test_predictions_file = os.path.join(predictions_dir, f'fold_{fold}_test_predictions.csv')
        with open(test_predictions_file, 'w', newline='') as f:
            writer = csv.writer(f)
            writer.writerow(['original_index', 'true_value', 'predicted_value', 'error'])
            for idx, true_val, pred_val in zip(test_idx, y_test, pred_test):
                writer.writerow([idx, true_val, pred_val, abs(true_val - pred_val)])
        
        # ========== 保存训练集索引 ==========
        train_indices_file = os.path.join(predictions_dir, f'fold_{fold}_train_indices.npy')
        np.save(train_indices_file, train_idx)
        
        # ========== 保存验证集索引 ==========
        test_indices_file = os.path.join(predictions_dir, f'fold_{fold}_test_indices.npy')
        np.save(test_indices_file, test_idx)
        
        print(f"  ✓ 已保存模型: {model_path}")
        print(f"  ✓ 已保存训练集预测: {train_predictions_file}")
        print(f"  ✓ 已保存验证集预测: {test_predictions_file}")
        
        del model
        tf.keras.backend.clear_session()
    
    # 保存汇总结果
    serializable_params = best_params.copy()
    for key in ['conv_filters', 'dense_units']:
        if key in serializable_params:
            serializable_params[key] = list(serializable_params[key])
    
    summary = {
        'R2_mean': float(np.mean(all_r2)),
        'R2_std': float(np.std(all_r2)),
        'MAE_mean': float(np.mean(all_mae)),
        'MAE_std': float(np.std(all_mae)),
        'RMSE_mean': float(np.mean(all_rmse)),
        'RMSE_std': float(np.std(all_rmse)),
        'best_params': serializable_params
    }
    
    with open(os.path.join(output_dir, 'summary.json'), 'w', encoding='utf-8') as f:
        json.dump(summary, f, indent=2, ensure_ascii=False)
    
    print("\n" + "="*60)
    print("最佳模型训练完成!")
    print("="*60)
    print(f"\n总体结果:")
    print(f"  R²:   {np.mean(all_r2):.4f} ± {np.std(all_r2):.4f}")
    print(f"  MAE:  {np.mean(all_mae):.4f} ± {np.std(all_mae):.4f}")
    print(f"  RMSE: {np.mean(all_rmse):.4f} ± {np.std(all_rmse):.4f}")
    print(f"\n结果保存位置:")
    print(f"  - 模型文件: {output_dir}/best_model_fold_*.h5")
    print(f"  - 预测结果: {predictions_dir}/")
    print(f"  - 汇总信息: {output_dir}/summary.json")
    print(f"  - 训练结果: {output_dir}/training_results.csv")
    
    return summary

# ============================================================================
# 4. 主函数
# ============================================================================
def main():
    """使用最佳参数进行训练"""
    print("="*60)
    print("CNN最佳参数训练 - 高熵合金硬度预测")
    print("="*60)
    
    # 加载数据
    X_all, Y_all, data_info = load_embedding_data()
    
    # 最佳参数（来自调参结果）
    best_params = {
        'conv_filters': [12, 28, 56],
        'dense_units': [256, 128, 64, 16],
        'kernel_size': (5, 5),
        'learning_rate': 0.00010956749686519973,
        'batch_size': 12,
        'dropout_rate': 0.0097086836073558,
        'use_batch_norm': True,
        'activation': 'selu'
    }
    
    # 训练模型
    summary = train_with_best_params(X_all, Y_all, best_params, output_dir=output_dir)
    
    print("\n" + "="*60)
    print("所有任务完成!")
    print("="*60)

if __name__ == "__main__":
    main()

2025-12-14 12:23:22.647350: I tensorflow/core/util/util.cc:169] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.


CNN最佳参数训练 - 高熵合金硬度预测
加载数据...
✓ 数据加载完成
  样本数量: 483
  嵌入矩阵形状: (483, 21, 768)
  HV值范围: [109.00, 1084.00]
  调整后形状: (483, 1, 21, 768)

使用最佳参数进行完整训练

最佳参数:
  conv_filters: [12, 28, 56]
  dense_units: [256, 128, 64, 16]
  kernel_size: (5, 5)
  learning_rate: 0.00010956749686519973
  batch_size: 12
  dropout_rate: 0.0097086836073558
  use_batch_norm: True
  activation: selu

第 1/10 折


2025-12-14 12:23:25.174276: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F AVX512_VNNI AVX512_BF16 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-12-14 12:23:25.801927: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1532] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 22034 MB memory:  -> device: 0, name: NVIDIA GeForce RTX 4090 D, pci bus id: 0000:02:00.0, compute capability: 8.9


Epoch 1/500


2025-12-14 12:23:27.260908: I tensorflow/stream_executor/cuda/cuda_dnn.cc:384] Loaded cuDNN version 8101
2025-12-14 12:23:27.923928: W tensorflow/stream_executor/gpu/asm_compiler.cc:230] Falling back to the CUDA driver for PTX compilation; ptxas does not support CC 8.9
2025-12-14 12:23:27.923965: W tensorflow/stream_executor/gpu/asm_compiler.cc:233] Used ptxas at ptxas
2025-12-14 12:23:27.924112: W tensorflow/stream_executor/gpu/redzone_allocator.cc:314] UNIMPLEMENTED: ptxas ptxas too old. Falling back to the driver to compile.
Relying on driver to perform ptx compilation. 
Modify $PATH to customize ptxas location.
This message will be only logged once.
2025-12-14 12:23:28.477251: I tensorflow/stream_executor/cuda/cuda_blas.cc:1786] TensorFloat-32 will be used for the matrix multiplication. This will only be logged once.


37/37 [==============================] - ETA: 0s - loss: 164350.1250 - root_mean_squared_error: 405.4012 - mean_absolute_error: 342.9235
Epoch 1: val_loss improved from inf to 236218.95312, saving model to ./best_model_final_0/best_model_fold_0.h5
37/37 [==============================] - 3s 21ms/step - loss: 164350.1250 - root_mean_squared_error: 405.4012 - mean_absolute_error: 342.9235 - val_loss: 236218.9531 - val_root_mean_squared_error: 486.0236 - val_mean_absolute_error: 436.8827
Epoch 2/500
34/37 [==========================>...] - ETA: 0s - loss: 27361.8438 - root_mean_squared_error: 165.4142 - mean_absolute_error: 131.2768
Epoch 2: val_loss improved from 236218.95312 to 228381.34375, saving model to ./best_model_final_0/best_model_fold_0.h5
37/37 [==============================] - 1s 15ms/step - loss: 26935.8320 - root_mean_squared_error: 164.1214 - mean_absolute_error: 130.2762 - val_loss: 228381.3438 - val_root_mean_squared_error: 477.8926 - val_mean_absolute_error: 432.3725
E

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



Epoch 42/500
37/37 [==============================] - ETA: 0s - loss: 2874.9231 - root_mean_squared_error: 53.6183 - mean_absolute_error: 38.6422
Epoch 42: val_loss improved from 2003.54480 to 1983.38049, saving model to ./best_model_final_0/best_model_fold_7.h5
37/37 [==============================] - 1s 14ms/step - loss: 2874.9231 - root_mean_squared_error: 53.6183 - mean_absolute_error: 38.6422 - val_loss: 1983.3805 - val_root_mean_squared_error: 44.5352 - val_mean_absolute_error: 33.6658
Epoch 43/500
36/37 [============================>.] - ETA: 0s - loss: 2536.8108 - root_mean_squared_error: 50.3668 - mean_absolute_error: 37.8119
Epoch 43: val_loss improved from 1983.38049 to 1479.46375, saving model to ./best_model_final_0/best_model_fold_7.h5
37/37 [==============================] - 0s 11ms/step - loss: 2521.2949 - root_mean_squared_error: 50.2125 - mean_absolute_error: 37.6606 - val_loss: 1479.4637 - val_root_mean_squared_error: 38.4638 - val_mean_absolute_error: 27.6892
Epoch 

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [ ]:
# 在所有导入之前
import os
os.environ['PYTHONHASHSEED'] = '42'
os.environ['TF_DETERMINISTIC_OPS'] = '1'
os.environ['TF_CUDNN_DETERMINISTIC'] = '1'

# 然后再导入其他库
import numpy as np
import tensorflow as tf
import os
import json
import csv
import matplotlib.pyplot as plt
from sklearn.model_selection import KFold
from sklearn.metrics import mean_absolute_error, mean_squared_error
import tensorflow as tf
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout, BatchNormalization

# 设置中文字体
import matplotlib
matplotlib.rcParams['font.sans-serif'] = ['SimHei', 'DejaVu Sans']
matplotlib.rcParams['axes.unicode_minus'] = False

# 2. 在set_random_seeds函数中添加GPU配置
def set_random_seeds(seed):
    """设置所有可能的随机种子"""
    import random
    random.seed(seed)
    np.random.seed(seed)
    tf.random.set_seed(seed)
    
    os.environ['TF_DETERMINISTIC_OPS'] = '1'
    os.environ['TF_CUDNN_DETERMINISTIC'] = '1'
    os.environ['PYTHONHASHSEED'] = str(seed)
    
    tf.keras.utils.set_random_seed(seed)
    tf.config.experimental.enable_op_determinism()
    
    # 添加GPU内存配置
    gpus = tf.config.list_physical_devices('GPU')
    if gpus:
        try:
            for gpu in gpus:
                tf.config.experimental.set_memory_growth(gpu, True)
        except RuntimeError as e:
            print(f"GPU配置警告: {e}")

# 设置随机种子
SEED = 42
set_random_seeds(SEED)

# 输入输出目录
output_dir = './best_model_final_1'


# ============================================================================
# 1. 数据加载函数
# ============================================================================
def load_embedding_data(data_dir='..//..//二维高熵合金数据'):
    """加载生成的嵌入矩阵数据"""
    print("="*60)
    print("加载数据...")
    print("="*60)
    
    embedding_path = os.path.join(data_dir, 'alloy_embedding_matrices.npy')
    X_all = np.load(embedding_path)
    
    hv_path = os.path.join(data_dir, 'HV_values.npy')
    Y_all = np.load(hv_path)
    
    info_path = os.path.join(data_dir, 'data_info.json')
    with open(info_path, 'r', encoding='utf-8') as f:
        data_info = json.load(f)
    
    print(f"✓ 数据加载完成")
    print(f"  样本数量: {len(X_all)}")
    print(f"  嵌入矩阵形状: {X_all.shape}")
    print(f"  HV值范围: [{Y_all.min():.2f}, {Y_all.max():.2f}]")
    
    X_all = np.expand_dims(X_all, axis=1)
    print(f"  调整后形状: {X_all.shape}")
    
    return X_all, Y_all, data_info

# ============================================================================
# 2. CNN模型构建函数
# ============================================================================
def build_cnn_model(input_shape, hyperparams):
    """根据超参数构建CNN模型"""
    model = Sequential()
    
    conv_filters = hyperparams['conv_filters']
    kernel_size = hyperparams['kernel_size']
    use_batch_norm = hyperparams['use_batch_norm']
    dropout_rate = hyperparams['dropout_rate']
    activation = hyperparams['activation']
    
    # 第一个卷积层
    model.add(Conv2D(
        filters=conv_filters[0],
        kernel_size=kernel_size,
        strides=1,
        padding='same',
        data_format='channels_first',
        activation=activation,
        input_shape=input_shape
    ))
    if use_batch_norm:
        model.add(BatchNormalization(axis=1))
    model.add(MaxPooling2D(pool_size=(2, 2), strides=2, padding='same', 
                           data_format='channels_first'))
    
    # 第二个卷积层
    model.add(Conv2D(conv_filters[1], kernel_size, strides=1, padding='same',
                     data_format='channels_first', activation=activation))
    if use_batch_norm:
        model.add(BatchNormalization(axis=1))
    model.add(MaxPooling2D((2, 2), 2, 'same', data_format='channels_first'))
    
    # 第三个卷积层
    model.add(Conv2D(conv_filters[2], kernel_size, strides=1, padding='same',
                     data_format='channels_first', activation=activation))
    if use_batch_norm:
        model.add(BatchNormalization(axis=1))
    model.add(MaxPooling2D((2, 2), 2, 'same', data_format='channels_first'))
    
    # 展平
    model.add(Flatten())
    
    # 全连接层
    dense_units = hyperparams['dense_units']
    for units in dense_units:
        model.add(Dense(units, activation=activation))
        if dropout_rate > 0:
            model.add(Dropout(dropout_rate))
    
    # 输出层
    model.add(Dense(1, activation='linear'))
    
    # 编译模型
    adam = Adam(learning_rate=hyperparams['learning_rate'])
    model.compile(
        optimizer=adam, 
        loss='mean_squared_error',
        metrics=[
            tf.keras.metrics.RootMeanSquaredError(),
            tf.keras.metrics.MeanAbsoluteError()
        ]
    )
    
    return model

# ============================================================================
# 3. 使用最佳参数进行完整训练
# ============================================================================
def train_with_best_params(X_all, Y_all, best_params, output_dir='./best_model_results'):
    """使用最佳参数进行完整的十折交叉验证训练"""
    os.makedirs(output_dir, exist_ok=True)
    
    print("\n" + "="*60)
    print("使用最佳参数进行完整训练")
    print("="*60)
    print(f"\n最佳参数:")
    for k, v in best_params.items():
        if k in ['conv_filters', 'dense_units']:
            print(f"  {k}: {list(v)}")
        else:
            print(f"  {k}: {v}")
    print("="*60)
    
    kf = KFold(n_splits=10, random_state=2*10+55, shuffle=True)
    
    all_rmse = []
    all_mae = []
    all_r2 = []
    
    results_file = os.path.join(output_dir, 'training_results.csv')
    with open(results_file, 'w', newline='') as f:
        writer = csv.writer(f)
        writer.writerow(['fold', 'loss_train', 'loss_test', 'r_train', 
                        'r_test', 'mae', 'rmse'])
    
    # 创建每折预测结果保存目录
    predictions_dir = os.path.join(output_dir, 'fold_predictions')
    os.makedirs(predictions_dir, exist_ok=True)
    
    for fold, (train_idx, test_idx) in enumerate(kf.split(X_all)):
        print(f"\n第 {fold + 1}/10 折")
        
        x_train, x_test = X_all[train_idx], X_all[test_idx]
        y_train, y_test = Y_all[train_idx], Y_all[test_idx]
        
        # 保存每折的模型
        model_path = os.path.join(output_dir, f'best_model_fold_{fold}.h5')
        
        callbacks = [
            # EarlyStopping(
            #     monitor='val_loss',
            #     patience=30,
            #     min_delta=0.0001,
            #     restore_best_weights=True,
            #     verbose=1,
            #     mode='min'
            # ),
            ModelCheckpoint(
                filepath=model_path,
                monitor='val_loss',
                save_best_only=True,
                mode='min',
                verbose=1
            )
        ]
        
        input_shape = x_train.shape[1:]
        model = build_cnn_model(input_shape, best_params)
        
        history = model.fit(
            x_train, y_train,
            epochs=500,
            batch_size=best_params['batch_size'],
            validation_data=(x_train, y_train),
            callbacks=callbacks,
            verbose=1
        )
        
        # 加载最佳模型
        model = load_model(model_path)
        
        loss_train, rmse_train, mae_train = model.evaluate(x_train, y_train, verbose=0)
        loss_test, rmse_test, mae_test = model.evaluate(x_test, y_test, verbose=0)
        
        # 预测
        pred_train = model.predict(x_train, batch_size=best_params['batch_size'], verbose=0).reshape(-1)
        pred_test = model.predict(x_test, batch_size=best_params['batch_size'], verbose=0).reshape(-1)
        
        r_train = np.corrcoef(pred_train, y_train)[0, 1]
        r_test = np.corrcoef(pred_test, y_test)[0, 1]
        
        mae = mean_absolute_error(y_test, pred_test)
        rmse = mean_squared_error(y_test, pred_test) ** 0.5
        
        all_rmse.append(rmse)
        all_mae.append(mae)
        all_r2.append(r_test)
        
        print(f"  测试集 R: {r_test:.4f}, MAE: {mae:.4f}, RMSE: {rmse:.4f}")
        
        with open(results_file, 'a', newline='') as f:
            writer = csv.writer(f)
            writer.writerow([fold, loss_train, loss_test, r_train, r_test, mae, rmse])
        
        # ========== 保存训练集预测结果 ==========
        train_predictions_file = os.path.join(predictions_dir, f'fold_{fold}_train_predictions.csv')
        with open(train_predictions_file, 'w', newline='') as f:
            writer = csv.writer(f)
            writer.writerow(['original_index', 'true_value', 'predicted_value', 'error'])
            for idx, true_val, pred_val in zip(train_idx, y_train, pred_train):
                writer.writerow([idx, true_val, pred_val, abs(true_val - pred_val)])
        
        # ========== 保存验证集(测试集)预测结果 ==========
        test_predictions_file = os.path.join(predictions_dir, f'fold_{fold}_test_predictions.csv')
        with open(test_predictions_file, 'w', newline='') as f:
            writer = csv.writer(f)
            writer.writerow(['original_index', 'true_value', 'predicted_value', 'error'])
            for idx, true_val, pred_val in zip(test_idx, y_test, pred_test):
                writer.writerow([idx, true_val, pred_val, abs(true_val - pred_val)])
        
        # ========== 保存训练集索引 ==========
        train_indices_file = os.path.join(predictions_dir, f'fold_{fold}_train_indices.npy')
        np.save(train_indices_file, train_idx)
        
        # ========== 保存验证集索引 ==========
        test_indices_file = os.path.join(predictions_dir, f'fold_{fold}_test_indices.npy')
        np.save(test_indices_file, test_idx)
        
        print(f"  ✓ 已保存模型: {model_path}")
        print(f"  ✓ 已保存训练集预测: {train_predictions_file}")
        print(f"  ✓ 已保存验证集预测: {test_predictions_file}")
        
        del model
        tf.keras.backend.clear_session()
    
    # 保存汇总结果
    serializable_params = best_params.copy()
    for key in ['conv_filters', 'dense_units']:
        if key in serializable_params:
            serializable_params[key] = list(serializable_params[key])
    
    summary = {
        'R2_mean': float(np.mean(all_r2)),
        'R2_std': float(np.std(all_r2)),
        'MAE_mean': float(np.mean(all_mae)),
        'MAE_std': float(np.std(all_mae)),
        'RMSE_mean': float(np.mean(all_rmse)),
        'RMSE_std': float(np.std(all_rmse)),
        'best_params': serializable_params
    }
    
    with open(os.path.join(output_dir, 'summary.json'), 'w', encoding='utf-8') as f:
        json.dump(summary, f, indent=2, ensure_ascii=False)
    
    print("\n" + "="*60)
    print("最佳模型训练完成!")
    print("="*60)
    print(f"\n总体结果:")
    print(f"  R²:   {np.mean(all_r2):.4f} ± {np.std(all_r2):.4f}")
    print(f"  MAE:  {np.mean(all_mae):.4f} ± {np.std(all_mae):.4f}")
    print(f"  RMSE: {np.mean(all_rmse):.4f} ± {np.std(all_rmse):.4f}")
    print(f"\n结果保存位置:")
    print(f"  - 模型文件: {output_dir}/best_model_fold_*.h5")
    print(f"  - 预测结果: {predictions_dir}/")
    print(f"  - 汇总信息: {output_dir}/summary.json")
    print(f"  - 训练结果: {output_dir}/training_results.csv")
    
    return summary

# ============================================================================
# 4. 主函数
# ============================================================================
def main():
    """使用最佳参数进行训练"""
    print("="*60)
    print("CNN最佳参数训练 - 高熵合金硬度预测")
    print("="*60)
    
    # 加载数据
    X_all, Y_all, data_info = load_embedding_data()
    
    # 最佳参数（来自调参结果）
    best_params = {
        'conv_filters': [12, 28, 56],
        'dense_units': [256, 128, 64, 16],
        'kernel_size': (5, 5),
        'learning_rate': 0.00010956749686519973,
        'batch_size': 12,
        'dropout_rate': 0.0097086836073558,
        'use_batch_norm': True,
        'activation': 'selu'
    }
    
    # 训练模型
    summary = train_with_best_params(X_all, Y_all, best_params, output_dir=output_dir)
    
    print("\n" + "="*60)
    print("所有任务完成!")
    print("="*60)

if __name__ == "__main__":
    main()

GPU配置警告: Physical devices cannot be modified after being initialized
CNN最佳参数训练 - 高熵合金硬度预测
加载数据...
✓ 数据加载完成
  样本数量: 483
  嵌入矩阵形状: (483, 21, 768)
  HV值范围: [109.00, 1084.00]
  调整后形状: (483, 1, 21, 768)

使用最佳参数进行完整训练

最佳参数:
  conv_filters: [12, 28, 56]
  dense_units: [256, 128, 64, 16]
  kernel_size: (5, 5)
  learning_rate: 0.00010956749686519973
  batch_size: 12
  dropout_rate: 0.0097086836073558
  use_batch_norm: True
  activation: selu

第 1/10 折
Epoch 1/500
37/37 [==============================] - ETA: 0s - loss: 130280.8125 - root_mean_squared_error: 360.9443 - mean_absolute_error: 292.3859
Epoch 1: val_loss improved from inf to 226864.65625, saving model to ./best_model_final_1/best_model_fold_0.h5
37/37 [==============================] - 1s 19ms/step - loss: 130280.8125 - root_mean_squared_error: 360.9443 - mean_absolute_error: 292.3859 - val_loss: 226864.6562 - val_root_mean_squared_error: 476.3031 - val_mean_absolute_error: 426.2698
Epoch 2/500
35/37 [===========================>..]

In [ ]:
# 在所有导入之前
import os
os.environ['PYTHONHASHSEED'] = '42'
os.environ['TF_DETERMINISTIC_OPS'] = '1'
os.environ['TF_CUDNN_DETERMINISTIC'] = '1'

# 然后再导入其他库
import numpy as np
import tensorflow as tf
import os
import json
import csv
import matplotlib.pyplot as plt
from sklearn.model_selection import KFold
from sklearn.metrics import mean_absolute_error, mean_squared_error
import tensorflow as tf
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout, BatchNormalization

# 设置中文字体
import matplotlib
matplotlib.rcParams['font.sans-serif'] = ['SimHei', 'DejaVu Sans']
matplotlib.rcParams['axes.unicode_minus'] = False

# 2. 在set_random_seeds函数中添加GPU配置
def set_random_seeds(seed):
    """设置所有可能的随机种子"""
    import random
    random.seed(seed)
    np.random.seed(seed)
    tf.random.set_seed(seed)
    
    os.environ['TF_DETERMINISTIC_OPS'] = '1'
    os.environ['TF_CUDNN_DETERMINISTIC'] = '1'
    os.environ['PYTHONHASHSEED'] = str(seed)
    
    tf.keras.utils.set_random_seed(seed)
    tf.config.experimental.enable_op_determinism()
    
    # 添加GPU内存配置
    gpus = tf.config.list_physical_devices('GPU')
    if gpus:
        try:
            for gpu in gpus:
                tf.config.experimental.set_memory_growth(gpu, True)
        except RuntimeError as e:
            print(f"GPU配置警告: {e}")

# 设置随机种子
SEED = 56
set_random_seeds(SEED)

# 输入输出目录
output_dir = './best_model_final_2'


# ============================================================================
# 1. 数据加载函数
# ============================================================================
def load_embedding_data(data_dir='..//..//二维高熵合金数据'):
    """加载生成的嵌入矩阵数据"""
    print("="*60)
    print("加载数据...")
    print("="*60)
    
    embedding_path = os.path.join(data_dir, 'alloy_embedding_matrices.npy')
    X_all = np.load(embedding_path)
    
    hv_path = os.path.join(data_dir, 'HV_values.npy')
    Y_all = np.load(hv_path)
    
    info_path = os.path.join(data_dir, 'data_info.json')
    with open(info_path, 'r', encoding='utf-8') as f:
        data_info = json.load(f)
    
    print(f"✓ 数据加载完成")
    print(f"  样本数量: {len(X_all)}")
    print(f"  嵌入矩阵形状: {X_all.shape}")
    print(f"  HV值范围: [{Y_all.min():.2f}, {Y_all.max():.2f}]")
    
    X_all = np.expand_dims(X_all, axis=1)
    print(f"  调整后形状: {X_all.shape}")
    
    return X_all, Y_all, data_info

# ============================================================================
# 2. CNN模型构建函数
# ============================================================================
def build_cnn_model(input_shape, hyperparams):
    """根据超参数构建CNN模型"""
    model = Sequential()
    
    conv_filters = hyperparams['conv_filters']
    kernel_size = hyperparams['kernel_size']
    use_batch_norm = hyperparams['use_batch_norm']
    dropout_rate = hyperparams['dropout_rate']
    activation = hyperparams['activation']
    
    # 第一个卷积层
    model.add(Conv2D(
        filters=conv_filters[0],
        kernel_size=kernel_size,
        strides=1,
        padding='same',
        data_format='channels_first',
        activation=activation,
        input_shape=input_shape
    ))
    if use_batch_norm:
        model.add(BatchNormalization(axis=1))
    model.add(MaxPooling2D(pool_size=(2, 2), strides=2, padding='same', 
                           data_format='channels_first'))
    
    # 第二个卷积层
    model.add(Conv2D(conv_filters[1], kernel_size, strides=1, padding='same',
                     data_format='channels_first', activation=activation))
    if use_batch_norm:
        model.add(BatchNormalization(axis=1))
    model.add(MaxPooling2D((2, 2), 2, 'same', data_format='channels_first'))
    
    # 第三个卷积层
    model.add(Conv2D(conv_filters[2], kernel_size, strides=1, padding='same',
                     data_format='channels_first', activation=activation))
    if use_batch_norm:
        model.add(BatchNormalization(axis=1))
    model.add(MaxPooling2D((2, 2), 2, 'same', data_format='channels_first'))
    
    # 展平
    model.add(Flatten())
    
    # 全连接层
    dense_units = hyperparams['dense_units']
    for units in dense_units:
        model.add(Dense(units, activation=activation))
        if dropout_rate > 0:
            model.add(Dropout(dropout_rate))
    
    # 输出层
    model.add(Dense(1, activation='linear'))
    
    # 编译模型
    adam = Adam(learning_rate=hyperparams['learning_rate'])
    model.compile(
        optimizer=adam, 
        loss='mean_squared_error',
        metrics=[
            tf.keras.metrics.RootMeanSquaredError(),
            tf.keras.metrics.MeanAbsoluteError()
        ]
    )
    
    return model

# ============================================================================
# 3. 使用最佳参数进行完整训练
# ============================================================================
def train_with_best_params(X_all, Y_all, best_params, output_dir='./best_model_results'):
    """使用最佳参数进行完整的十折交叉验证训练"""
    os.makedirs(output_dir, exist_ok=True)
    
    print("\n" + "="*60)
    print("使用最佳参数进行完整训练")
    print("="*60)
    print(f"\n最佳参数:")
    for k, v in best_params.items():
        if k in ['conv_filters', 'dense_units']:
            print(f"  {k}: {list(v)}")
        else:
            print(f"  {k}: {v}")
    print("="*60)
    
    kf = KFold(n_splits=10, random_state=2*10+55, shuffle=True)
    
    all_rmse = []
    all_mae = []
    all_r2 = []
    
    results_file = os.path.join(output_dir, 'training_results.csv')
    with open(results_file, 'w', newline='') as f:
        writer = csv.writer(f)
        writer.writerow(['fold', 'loss_train', 'loss_test', 'r_train', 
                        'r_test', 'mae', 'rmse'])
    
    # 创建每折预测结果保存目录
    predictions_dir = os.path.join(output_dir, 'fold_predictions')
    os.makedirs(predictions_dir, exist_ok=True)
    
    for fold, (train_idx, test_idx) in enumerate(kf.split(X_all)):
        print(f"\n第 {fold + 1}/10 折")
        
        x_train, x_test = X_all[train_idx], X_all[test_idx]
        y_train, y_test = Y_all[train_idx], Y_all[test_idx]
        
        # 保存每折的模型
        model_path = os.path.join(output_dir, f'best_model_fold_{fold}.h5')
        
        callbacks = [
            # EarlyStopping(
            #     monitor='val_loss',
            #     patience=30,
            #     min_delta=0.0001,
            #     restore_best_weights=True,
            #     verbose=1,
            #     mode='min'
            # ),
            ModelCheckpoint(
                filepath=model_path,
                monitor='val_loss',
                save_best_only=True,
                mode='min',
                verbose=1
            )
        ]
        
        input_shape = x_train.shape[1:]
        model = build_cnn_model(input_shape, best_params)
        
        history = model.fit(
            x_train, y_train,
            epochs=500,
            batch_size=best_params['batch_size'],
            validation_data=(x_train, y_train),
            callbacks=callbacks,
            verbose=1
        )
        
        # 加载最佳模型
        model = load_model(model_path)
        
        loss_train, rmse_train, mae_train = model.evaluate(x_train, y_train, verbose=0)
        loss_test, rmse_test, mae_test = model.evaluate(x_test, y_test, verbose=0)
        
        # 预测
        pred_train = model.predict(x_train, batch_size=best_params['batch_size'], verbose=0).reshape(-1)
        pred_test = model.predict(x_test, batch_size=best_params['batch_size'], verbose=0).reshape(-1)
        
        r_train = np.corrcoef(pred_train, y_train)[0, 1]
        r_test = np.corrcoef(pred_test, y_test)[0, 1]
        
        mae = mean_absolute_error(y_test, pred_test)
        rmse = mean_squared_error(y_test, pred_test) ** 0.5
        
        all_rmse.append(rmse)
        all_mae.append(mae)
        all_r2.append(r_test)
        
        print(f"  测试集 R: {r_test:.4f}, MAE: {mae:.4f}, RMSE: {rmse:.4f}")
        
        with open(results_file, 'a', newline='') as f:
            writer = csv.writer(f)
            writer.writerow([fold, loss_train, loss_test, r_train, r_test, mae, rmse])
        
        # ========== 保存训练集预测结果 ==========
        train_predictions_file = os.path.join(predictions_dir, f'fold_{fold}_train_predictions.csv')
        with open(train_predictions_file, 'w', newline='') as f:
            writer = csv.writer(f)
            writer.writerow(['original_index', 'true_value', 'predicted_value', 'error'])
            for idx, true_val, pred_val in zip(train_idx, y_train, pred_train):
                writer.writerow([idx, true_val, pred_val, abs(true_val - pred_val)])
        
        # ========== 保存验证集(测试集)预测结果 ==========
        test_predictions_file = os.path.join(predictions_dir, f'fold_{fold}_test_predictions.csv')
        with open(test_predictions_file, 'w', newline='') as f:
            writer = csv.writer(f)
            writer.writerow(['original_index', 'true_value', 'predicted_value', 'error'])
            for idx, true_val, pred_val in zip(test_idx, y_test, pred_test):
                writer.writerow([idx, true_val, pred_val, abs(true_val - pred_val)])
        
        # ========== 保存训练集索引 ==========
        train_indices_file = os.path.join(predictions_dir, f'fold_{fold}_train_indices.npy')
        np.save(train_indices_file, train_idx)
        
        # ========== 保存验证集索引 ==========
        test_indices_file = os.path.join(predictions_dir, f'fold_{fold}_test_indices.npy')
        np.save(test_indices_file, test_idx)
        
        print(f"  ✓ 已保存模型: {model_path}")
        print(f"  ✓ 已保存训练集预测: {train_predictions_file}")
        print(f"  ✓ 已保存验证集预测: {test_predictions_file}")
        
        del model
        tf.keras.backend.clear_session()
    
    # 保存汇总结果
    serializable_params = best_params.copy()
    for key in ['conv_filters', 'dense_units']:
        if key in serializable_params:
            serializable_params[key] = list(serializable_params[key])
    
    summary = {
        'R2_mean': float(np.mean(all_r2)),
        'R2_std': float(np.std(all_r2)),
        'MAE_mean': float(np.mean(all_mae)),
        'MAE_std': float(np.std(all_mae)),
        'RMSE_mean': float(np.mean(all_rmse)),
        'RMSE_std': float(np.std(all_rmse)),
        'best_params': serializable_params
    }
    
    with open(os.path.join(output_dir, 'summary.json'), 'w', encoding='utf-8') as f:
        json.dump(summary, f, indent=2, ensure_ascii=False)
    
    print("\n" + "="*60)
    print("最佳模型训练完成!")
    print("="*60)
    print(f"\n总体结果:")
    print(f"  R²:   {np.mean(all_r2):.4f} ± {np.std(all_r2):.4f}")
    print(f"  MAE:  {np.mean(all_mae):.4f} ± {np.std(all_mae):.4f}")
    print(f"  RMSE: {np.mean(all_rmse):.4f} ± {np.std(all_rmse):.4f}")
    print(f"\n结果保存位置:")
    print(f"  - 模型文件: {output_dir}/best_model_fold_*.h5")
    print(f"  - 预测结果: {predictions_dir}/")
    print(f"  - 汇总信息: {output_dir}/summary.json")
    print(f"  - 训练结果: {output_dir}/training_results.csv")
    
    return summary

# ============================================================================
# 4. 主函数
# ============================================================================
def main():
    """使用最佳参数进行训练"""
    print("="*60)
    print("CNN最佳参数训练 - 高熵合金硬度预测")
    print("="*60)
    
    # 加载数据
    X_all, Y_all, data_info = load_embedding_data()
    
    # 最佳参数（来自调参结果）
    best_params = {
        'conv_filters': [12, 28, 56],
        'dense_units': [256, 128, 64, 16],
        'kernel_size': (5, 5),
        'learning_rate': 0.00010956749686519973,
        'batch_size': 12,
        'dropout_rate': 0.0097086836073558,
        'use_batch_norm': True,
        'activation': 'selu'
    }
    
    # 训练模型
    summary = train_with_best_params(X_all, Y_all, best_params, output_dir=output_dir)
    
    print("\n" + "="*60)
    print("所有任务完成!")
    print("="*60)

if __name__ == "__main__":
    main()

CNN最佳参数训练 - 高熵合金硬度预测
加载数据...
✓ 数据加载完成
  样本数量: 483
  嵌入矩阵形状: (483, 21, 768)
  HV值范围: [109.00, 1084.00]
  调整后形状: (483, 1, 21, 768)

使用最佳参数进行完整训练

最佳参数:
  conv_filters: [12, 28, 56]
  dense_units: [256, 128, 64, 16]
  kernel_size: (5, 5)
  learning_rate: 0.00010956749686519973
  batch_size: 12
  dropout_rate: 0.0097086836073558
  use_batch_norm: True
  activation: selu

第 1/10 折
Epoch 1/500
34/37 [==========================>...] - ETA: 0s - loss: 120468.8438 - root_mean_squared_error: 347.0862 - mean_absolute_error: 286.3592
Epoch 1: val_loss improved from inf to 211318.21875, saving model to ./best_model_final_2/best_model_fold_0.h5
37/37 [==============================] - 1s 20ms/step - loss: 115843.5078 - root_mean_squared_error: 340.3579 - mean_absolute_error: 279.4700 - val_loss: 211318.2188 - val_root_mean_squared_error: 459.6936 - val_mean_absolute_error: 407.5809
Epoch 2/500
34/37 [==========================>...] - ETA: 0s - loss: 24062.6133 - root_mean_squared_error: 155.1213 - m

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



33/37 [=========================>....] - ETA: 0s - loss: 1177.4734 - root_mean_squared_error: 34.3143 - mean_absolute_error: 24.5507
Epoch 198: val_loss did not improve from 445.17862
37/37 [==============================] - 0s 12ms/step - loss: 1276.4961 - root_mean_squared_error: 35.7281 - mean_absolute_error: 25.3858 - val_loss: 481.7736 - val_root_mean_squared_error: 21.9493 - val_mean_absolute_error: 15.6356
Epoch 199/500
37/37 [==============================] - ETA: 0s - loss: 1691.4904 - root_mean_squared_error: 41.1277 - mean_absolute_error: 30.4221
Epoch 199: val_loss did not improve from 445.17862
37/37 [==============================] - 0s 11ms/step - loss: 1691.4904 - root_mean_squared_error: 41.1277 - mean_absolute_error: 30.4221 - val_loss: 777.7542 - val_root_mean_squared_error: 27.8882 - val_mean_absolute_error: 19.8900
Epoch 200/500
36/37 [============================>.] - ETA: 0s - loss: 1272.2155 - root_mean_squared_error: 35.6681 - mean_absolute_error: 24.9094
Epoch